In [1]:
import numpy as np

In [2]:
from phevaluator.evaluator import evaluate_cards

p1 = evaluate_cards("2c", "3c", "4c", "5c", "As", "8s", "9s")
p2 = evaluate_cards("2c", "3c", "4c", "5c", "7s", "8s", "9s")

# Player 2 has a stronger hand

In [3]:
from deck.card import Card, Rank, Suit
from deck.deck import Deck

In [4]:
def sort_hand(hand: np.ndarray) -> np.ndarray:
    return np.array(sorted(hand, reverse=True, key=lambda x: (x.get_rank(), x.get_tag())))

In [5]:
def is_a_pair(hand: np.ndarray) -> bool:
    return hand[0].get_rank() == hand[1].get_rank()

def compare_starting_hands(hand_one: np.ndarray, hand_two: np.ndarray) -> int:
    """
    Return 1 if hand one is stronger than hand two, -1 if hand two stronger, 0 if equal
    """
    is_hand_one_a_pair = is_a_pair(hand_one)
    is_hand_two_a_pair = is_a_pair(hand_two)
    if is_hand_one_a_pair and not is_hand_two_a_pair:
        return 1
    elif not is_hand_one_a_pair and is_hand_two_a_pair:
        return -1
    elif is_hand_one_a_pair and is_hand_two_a_pair:
        rank_one = hand_one[0].get_rank()
        rank_two = hand_two[0].get_rank()
        if rank_one == rank_two:
            return 0
        if rank_one > rank_two:
            return 1
        else:
            return -1
    else:
        hand_one = sort_hand(hand_one)
        hand_two = sort_hand(hand_two)
        if hand_one[0].get_rank() > hand_two[0].get_rank():
            return 1
        elif hand_one[0].get_rank() < hand_two[0].get_rank():
            return -1
        else:
            if hand_one[1].get_rank() > hand_two[1].get_rank():
                return 1
            elif hand_one[1].get_rank() < hand_two[1].get_rank():
                return -1
            else:
                return 0

In [ ]:
def compute_initial_effective_hand_strengths(iterations: int, suited=False):
    if suited:
        shift = 1
        name = "s"
        second_suit = "c"
    else:
        shift = 0
        name = "o"
        second_suit = "s"
    effective_hand_strengths = {}
    for i, rank_one in enumerate(list(Rank)[::-1]):
        for rank_two in list(Rank)[::-1][i+shift:]:
            deck = Deck()
            cards = np.concatenate((deck.draw_card_by_tag(str(rank_one.value) + "c"), deck.draw_card_by_tag(str(rank_two.value) + second_suit)))
            wins = 0
            positive_potential = 0
            negative_potential = 0
            for _ in range(iterations):
                deck.shuffle()
                opponent_cards = deck.draw_cards(2)
                initial_advantage = compare_starting_hands(sort_hand(cards), sort_hand(opponent_cards))
                flop = deck.draw_cards(3)
                turn = deck.draw_cards(1)
                river = deck.draw_cards(1)
                my_strength = evaluate_cards(*[card.get_tag() for card in np.concatenate((cards, flop, turn, river))])
                opponent_strength = evaluate_cards(*[card.get_tag() for card in np.concatenate((opponent_cards, flop, turn, river))])
                if my_strength < opponent_strength:
                    wins += 1
                    if initial_advantage == -1:
                        positive_potential += 1 #won the hand with initial disadvantage
                    elif initial_advantage == 0:
                        positive_potential += 0.5
                elif my_strength == opponent_strength: # draw
                    wins += 0.5
                    if initial_advantage == -1:
                        positive_potential += 0.5
                    elif initial_advantage == 1:
                        negative_potential += 0.5
                else: 
                    if initial_advantage == 1: #lost the hand with initial advantage
                        negative_potential += 1
                    elif initial_advantage == 0:
                        negative_potential += 0.5
                deck.return_cards(opponent_cards)
                deck.return_cards(flop)
                deck.return_cards(turn)
                deck.return_cards(river)
            effective_hand_strengths[str(rank_one.value) + str(rank_two.value) + name] = (wins * (iterations - negative_potential) + (iterations - wins) * positive_potential) / iterations ** 2
    return effective_hand_strengths

In [9]:
iterations = 100_000
suited_effective_hand_strength = compute_initial_effective_hand_strengths(iterations, True)
offsuit_effective_hand_strength = compute_initial_effective_hand_strengths(iterations, False)
effective_hand_strength = {
    **suited_effective_hand_strength,
    **offsuit_effective_hand_strength
}
for k,v in sorted(effective_hand_strength.items(), key=lambda item: item[1], reverse=True):
    print(k, v)

AAo 0.725965082875
KKo 0.678422618225
QQo 0.6410408953
54s 0.6283910673
65s 0.624642675325
76s 0.6174152124
53s 0.6157683248
87s 0.61479867195
JJo 0.6102447037
43s 0.6097577808
64s 0.603667434075
75s 0.603393564275
98s 0.59991635275
86s 0.59776195365
52s 0.592415743125
42s 0.59144847905
63s 0.590535007625
74s 0.5894668814
32s 0.588535743425
T9s 0.5882059198
97s 0.584947747
54o 0.58491496425
76o 0.584138493325
65o 0.5826856142
85s 0.58100191
87o 0.5806196061
62s 0.576874136925
TTo 0.574220404125
T8s 0.5741334556
98o 0.57082955335
JTs 0.5707841645
96s 0.570280707125
53o 0.56961441315
43o 0.5691839432
73s 0.5681961762
75o 0.566462057325
84s 0.5656378123
64o 0.5647967464
86o 0.5617588438
T7s 0.5610289053
95s 0.559913271475
T9o 0.55912842
97o 0.5586515648
72s 0.5553314848
J9s 0.5539084433
63o 0.552372879
74o 0.5509358881
82s 0.550111621075
83s 0.5495907521
52o 0.54792350875
85o 0.5469843004
JTo 0.545487109375
42o 0.5454635278
T8o 0.54506342755
94s 0.5449397747
T6s 0.542150518425
J8s 0.54188

In [11]:
for k,v in sorted(effective_hand_strength.items(), key=lambda item: item[1], reverse=True):
    print(k,round(v, 2))

AAo 0.73
KKo 0.68
QQo 0.64
54s 0.63
65s 0.62
76s 0.62
53s 0.62
87s 0.61
JJo 0.61
43s 0.61
64s 0.6
75s 0.6
98s 0.6
86s 0.6
52s 0.59
42s 0.59
63s 0.59
74s 0.59
32s 0.59
T9s 0.59
97s 0.58
54o 0.58
76o 0.58
65o 0.58
85s 0.58
87o 0.58
62s 0.58
TTo 0.57
T8s 0.57
98o 0.57
JTs 0.57
96s 0.57
53o 0.57
43o 0.57
73s 0.57
75o 0.57
84s 0.57
64o 0.56
86o 0.56
T7s 0.56
95s 0.56
T9o 0.56
97o 0.56
72s 0.56
J9s 0.55
63o 0.55
74o 0.55
82s 0.55
83s 0.55
52o 0.55
85o 0.55
JTo 0.55
42o 0.55
T8o 0.55
94s 0.54
T6s 0.54
J8s 0.54
32o 0.54
QJs 0.54
QTs 0.54
93s 0.54
96o 0.54
92s 0.54
99o 0.53
62o 0.53
T5s 0.53
84o 0.53
T7o 0.53
T4s 0.53
73o 0.53
J9o 0.53
J7s 0.53
Q9s 0.52
T3s 0.52
95o 0.52
QJo 0.52
T2s 0.52
QTo 0.52
KQs 0.51
J6s 0.51
J8o 0.51
T6o 0.51
72o 0.51
J5s 0.51
KJs 0.51
83o 0.51
J4s 0.51
Q8s 0.51
82o 0.5
94o 0.5
93o 0.5
KTs 0.5
J3s 0.5
88o 0.5
T5o 0.5
J2s 0.5
J7o 0.5
Q9o 0.5
92o 0.5
T4o 0.49
Q7s 0.49
Q6s 0.49
T3o 0.49
KQo 0.49
K9s 0.49
Q5s 0.49
T2o 0.48
KJo 0.48
Q8o 0.48
Q4s 0.48
AKs 0.48
J6o 0.48
J5o 0.4

In [7]:
import itertools


In [8]:
def compare_hands_after_flop(hand_one: np.ndarray, hand_two: np.ndarray) -> int:
    hand_one_strength = evaluate_cards(*[card.get_tag() for card in hand_one])
    hand_two_strength = evaluate_cards(*[card.get_tag() for card in hand_two])
    if hand_one_strength < hand_two_strength:
        return 1
    elif hand_one_strength == hand_one_strength:
        return 0
    else:
        return -1

In [98]:
def calculate_post_flop_result(cards, opponent_cards, flop, turn, river, wins, positive_potential, negative_potential):
    initial_advantage = compare_hands_after_flop(
                        np.concatenate((cards, flop)),
                        np.concatenate((opponent_cards, flop)),
                    )
    final_result = compare_hands_after_flop(
        np.concatenate((cards, flop, turn, river)),
        np.concatenate((opponent_cards, flop, turn, river)),
    )
    if final_result == 1:
        wins += 1
        if initial_advantage == -1:
            positive_potential += (
                1  # won the hand with initial disadvantage
            )
        elif initial_advantage == 0:
            positive_potential += 0.5
    elif final_result == 0:  # draw
        wins += 0.5
        if initial_advantage == -1:
            positive_potential += 0.5
        elif initial_advantage == 1:
            negative_potential += 0.5
    else:
        if (
            initial_advantage == 1
        ):  # lost the hand with initial advantage
            negative_potential += 1
        elif initial_advantage == 0:
            negative_potential += 0.5
    return wins, positive_potential, negative_potential

In [120]:
def perform_n_posflop_iterations(iterations: int, deck: Deck, cards: np.ndarray, flop:np.ndarray):
    wins = 0
    positive_potential = 0
    negative_potential = 0
    for _ in range(iterations):
        deck.shuffle()
        opponent_cards = deck.draw_cards(2)
        turn = deck.draw_cards(1)
        river = deck.draw_cards(1)
        wins, positive_potential, negative_potential = (
            calculate_post_flop_result(
                cards,
                opponent_cards,
                flop,
                turn,
                river,
                wins,
                positive_potential,
                negative_potential,
            )
        )
        deck.return_cards(opponent_cards)
        deck.return_cards(turn)
        deck.return_cards(river)
    return wins, positive_potential, negative_potential

In [126]:
def compute_mono_flop_effective_hand_strengths_for_suited_cards(
    iterations: int, made_flush=True
):
    suited = "s"
    first_suit = "c"
    if made_flush:
        flush = "f"
        second_suit = first_suit
    else:
        flush = "n"
        second_suit = "s"
    effective_hand_strengths = {}
    for starting_hand in itertools.combinations(list(Rank)[::-1], 2):
        deck = Deck()
        cards = np.concatenate(
            (
                deck.draw_card_by_tag(str(starting_hand[0].value) + first_suit),
                deck.draw_card_by_tag(str(starting_hand[1].value) + first_suit),
            )
        )
        rank_list = list(Rank)
        if made_flush:
            rank_list.remove(starting_hand[0])
            rank_list.remove(starting_hand[1])
        possible_combinations = itertools.combinations(rank_list[::-1], 3)
        for combination in possible_combinations:
            flop = np.concatenate(
                (
                    deck.draw_card_by_tag(str(combination[0].value) + second_suit),
                    deck.draw_card_by_tag(str(combination[1].value) + second_suit),
                    deck.draw_card_by_tag(str(combination[2].value) + second_suit),
                )
            )
            wins, positive_potential, negative_potential = perform_n_posflop_iterations(iterations, deck, cards, flop)
            deck.return_cards(flop)
            effective_hand_strengths[
                str(starting_hand[0].value)
                + str(starting_hand[1].value)
                + suited
                + "_"
                + str(combination[0].value)
                + str(combination[1].value)
                + str(combination[2].value)
                + "_mono_"
                + flush
            ] = (
                wins * (iterations - negative_potential)
                + (iterations - wins) * positive_potential
            ) / iterations**2
    return effective_hand_strengths

In [127]:
flop_effective_hand_strength_mono_and_flush = compute_mono_flop_effective_hand_strengths_for_suited_cards(10, made_flush=True)

In [128]:
for k,v in sorted(flop_effective_hand_strength_mono_and_flush.items(), key=lambda item: item[1], reverse=True):
    print(k, v)

AKs_QJT_mono_f 1.0
AKs_QJ8_mono_f 1.0
AKs_QJ6_mono_f 1.0
AKs_QJ5_mono_f 1.0
AKs_QJ3_mono_f 1.0
AKs_QJ2_mono_f 1.0
AKs_QT8_mono_f 1.0
AKs_QT7_mono_f 1.0
AKs_QT5_mono_f 1.0
AKs_QT4_mono_f 1.0
AKs_QT3_mono_f 1.0
AKs_Q98_mono_f 1.0
AKs_Q97_mono_f 1.0
AKs_Q96_mono_f 1.0
AKs_Q94_mono_f 1.0
AKs_Q93_mono_f 1.0
AKs_Q92_mono_f 1.0
AKs_Q87_mono_f 1.0
AKs_Q86_mono_f 1.0
AKs_Q85_mono_f 1.0
AKs_Q84_mono_f 1.0
AKs_Q82_mono_f 1.0
AKs_Q76_mono_f 1.0
AKs_Q75_mono_f 1.0
AKs_Q74_mono_f 1.0
AKs_Q73_mono_f 1.0
AKs_Q72_mono_f 1.0
AKs_Q65_mono_f 1.0
AKs_Q64_mono_f 1.0
AKs_Q63_mono_f 1.0
AKs_Q62_mono_f 1.0
AKs_Q52_mono_f 1.0
AKs_Q43_mono_f 1.0
AKs_Q42_mono_f 1.0
AKs_Q32_mono_f 1.0
AKs_JT9_mono_f 1.0
AKs_JT8_mono_f 1.0
AKs_JT7_mono_f 1.0
AKs_JT6_mono_f 1.0
AKs_JT5_mono_f 1.0
AKs_JT4_mono_f 1.0
AKs_JT3_mono_f 1.0
AKs_JT2_mono_f 1.0
AKs_J98_mono_f 1.0
AKs_J97_mono_f 1.0
AKs_J96_mono_f 1.0
AKs_J95_mono_f 1.0
AKs_J94_mono_f 1.0
AKs_J93_mono_f 1.0
AKs_J92_mono_f 1.0
AKs_J87_mono_f 1.0
AKs_J86_mono_f 1.0
AKs_J84_mono

In [129]:
flop_effective_hand_strength_mono_and_nothing = compute_mono_flop_effective_hand_strengths_for_suited_cards(10, False)

In [130]:
for k,v in sorted(flop_effective_hand_strength_mono_and_nothing.items(), key=lambda item: item[1], reverse=True):
    print(k, v)

AKs_AJ3_mono_n 1.0
AKs_AT4_mono_n 1.0
AKs_KJ6_mono_n 1.0
AKs_K94_mono_n 1.0
AQs_AQ7_mono_n 1.0
AQs_AJ9_mono_n 1.0
AQs_A95_mono_n 1.0
AQs_A94_mono_n 1.0
AQs_A63_mono_n 1.0
AQs_A62_mono_n 1.0
AQs_Q76_mono_n 1.0
AJs_J82_mono_n 1.0
ATs_AT2_mono_n 1.0
A9s_A95_mono_n 1.0
A8s_AK8_mono_n 1.0
A8s_AJ6_mono_n 1.0
A8s_A98_mono_n 1.0
A8s_A84_mono_n 1.0
A8s_KJ8_mono_n 1.0
A6s_A82_mono_n 1.0
A5s_AK6_mono_n 1.0
A4s_A94_mono_n 1.0
A4s_A93_mono_n 1.0
A4s_A75_mono_n 1.0
A4s_A74_mono_n 1.0
A4s_A54_mono_n 1.0
A3s_AK6_mono_n 1.0
A2s_A96_mono_n 1.0
KQs_AJT_mono_n 1.0
KQs_KQ2_mono_n 1.0
KQs_KT7_mono_n 1.0
KQs_K43_mono_n 1.0
KQs_QT4_mono_n 1.0
KQs_Q95_mono_n 1.0
KJs_J76_mono_n 1.0
KJs_T92_mono_n 1.0
KTs_KT3_mono_n 1.0
KTs_K42_mono_n 1.0
K9s_AKT_mono_n 1.0
K9s_KT4_mono_n 1.0
K8s_KT8_mono_n 1.0
K8s_K83_mono_n 1.0
K8s_K32_mono_n 1.0
K7s_AK2_mono_n 1.0
K7s_KQ7_mono_n 1.0
K7s_K74_mono_n 1.0
K5s_K52_mono_n 1.0
K4s_K42_mono_n 1.0
K3s_KT3_mono_n 1.0
K2s_KJ7_mono_n 1.0
QJs_KJ8_mono_n 1.0
QTs_QT6_mono_n 1.0
QTs_Q92_mono

In [112]:
def create_a_list_of_lower_ranks(rank: Rank) -> list:
    return [x for x in list(Rank) if x < rank]

In [134]:
def compute_21_flop_effective_hand_strengths_for_suited_cards(
    iterations: int, flush_draw=True
):
    first_suit = "c"
    suited = "s"
    if flush_draw:
        flush = "d"
        second_suit = first_suit
        third_suit = "s"
    else:
        flush = "n"
        second_suit = "s"
        third_suit = "d"

    effective_hand_strengths = {}
    for starting_hand in itertools.combinations(list(Rank)[::-1], 2):
        deck = Deck()
        cards = np.concatenate(
            (
                deck.draw_card_by_tag(str(starting_hand[0].value) + first_suit),
                deck.draw_card_by_tag(str(starting_hand[1].value) + first_suit),
            )
        )
        # mono and flush
        rank_list = list(Rank)
        if flush_draw:
            rank_list.remove(starting_hand[0])
            rank_list.remove(starting_hand[1])
        possible_combinations = itertools.combinations(rank_list[::-1], 2)
        for combination in possible_combinations:
            third_suit_rank_list = [
                combination[0],
                combination[1],
            ] + create_a_list_of_lower_ranks(combination[1])[::-1]
            if flush_draw:
                if starting_hand[1] > combination[1]:
                    third_suit_rank_list = [starting_hand[0], starting_hand[1]] + third_suit_rank_list
                elif starting_hand[0] > combination[1]:
                    third_suit_rank_list = [starting_hand[0]] + third_suit_rank_list
            for rank in third_suit_rank_list:
                flop = np.concatenate(
                    (
                        deck.draw_card_by_tag(str(combination[0].value) + second_suit),
                        deck.draw_card_by_tag(str(combination[1].value) + second_suit),
                        deck.draw_card_by_tag(str(rank.value) + third_suit),
                    )
                )
                flop = sort_hand(flop)
                wins, positive_potential, negative_potential = perform_n_posflop_iterations(iterations, deck, cards, flop)
                deck.return_cards(flop)
                # if str(rank_one.value) + str(rank_two.value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush in effective_hand_strengths:
                #    raise ValueError(str(rank_one.value) + str(rank_two.value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush)
                effective_hand_strengths[
                    str(starting_hand[0].value)
                    + str(starting_hand[1].value)
                    + suited
                    + str(flop[0].rank.value)
                    + str(flop[1].rank.value)
                    + str(flop[2].rank.value)
                    + "_twoone_"
                    + flush
                ] = (
                    wins * (iterations - negative_potential)
                    + (iterations - wins) * positive_potential
                ) / iterations**2
    return effective_hand_strengths

In [135]:
flop_effective_hand_strength_two_one_and_flush_draw = compute_21_flop_effective_hand_strengths_for_suited_cards(10)

In [136]:
for k,v in flop_effective_hand_strength_two_one_and_flush_draw.items():
    print(k, v)
#for k,v in sorted(flop_effective_hand_strength_two_one_and_flush_draw.items(), key=lambda item: item[1], reverse=True):
#    print(k, round(v, 2))

AKsAQJ_twoone_d 0.855
AKsKQJ_twoone_d 0.9525
AKsQQJ_twoone_d 0.855
AKsQJJ_twoone_d 0.865
AKsQJT_twoone_d 1.0
AKsQJ9_twoone_d 0.8225
AKsQJ8_twoone_d 0.79
AKsQJ7_twoone_d 0.7875
AKsQJ6_twoone_d 0.91
AKsQJ5_twoone_d 0.955
AKsQJ4_twoone_d 0.875
AKsQJ3_twoone_d 0.8225
AKsQJ2_twoone_d 1.0
AKsAQT_twoone_d 0.905
AKsKQT_twoone_d 0.95
AKsQQT_twoone_d 0.8375
AKsQTT_twoone_d 0.815
AKsQT9_twoone_d 0.955
AKsQT8_twoone_d 0.92
AKsQT7_twoone_d 0.865
AKsQT6_twoone_d 0.8725
AKsQT5_twoone_d 0.72
AKsQT4_twoone_d 1.0
AKsQT3_twoone_d 0.71
AKsQT2_twoone_d 0.8225
AKsAQ9_twoone_d 1.0
AKsKQ9_twoone_d 1.0
AKsQQ9_twoone_d 0.87
AKsQ99_twoone_d 0.82
AKsQ98_twoone_d 0.9075
AKsQ97_twoone_d 0.78
AKsQ96_twoone_d 0.8225
AKsQ95_twoone_d 1.0
AKsQ94_twoone_d 0.905
AKsQ93_twoone_d 0.675
AKsQ92_twoone_d 0.815
AKsAQ8_twoone_d 0.7225
AKsKQ8_twoone_d 0.9025
AKsQQ8_twoone_d 0.8225
AKsQ88_twoone_d 0.9
AKsQ87_twoone_d 0.8225
AKsQ86_twoone_d 0.595
AKsQ85_twoone_d 0.9125
AKsQ84_twoone_d 0.81
AKsQ83_twoone_d 0.79
AKsQ82_twoone_d 0.687

In [137]:
flop_effective_hand_strength_two_one_and_no_draw = compute_21_flop_effective_hand_strengths_for_suited_cards(10, False)

In [138]:
for k,v in flop_effective_hand_strength_two_one_and_no_draw.items():
    print(k, v)

AKsAAK_twoone_n 1.0
AKsAKK_twoone_n 1.0
AKsAKQ_twoone_n 0.9025
AKsAKJ_twoone_n 0.855
AKsAKT_twoone_n 0.81
AKsAK9_twoone_n 1.0
AKsAK8_twoone_n 0.9025
AKsAK7_twoone_n 0.81
AKsAK6_twoone_n 0.81
AKsAK5_twoone_n 0.9025
AKsAK4_twoone_n 1.0
AKsAK3_twoone_n 1.0
AKsAK2_twoone_n 0.9025
AKsAAQ_twoone_n 1.0
AKsAQQ_twoone_n 0.855
AKsAQJ_twoone_n 0.765
AKsAQT_twoone_n 0.9025
AKsAQ9_twoone_n 0.9025
AKsAQ8_twoone_n 0.9025
AKsAQ7_twoone_n 0.68
AKsAQ6_twoone_n 0.81
AKsAQ5_twoone_n 0.95
AKsAQ4_twoone_n 0.765
AKsAQ3_twoone_n 0.855
AKsAQ2_twoone_n 0.9025
AKsAAJ_twoone_n 1.0
AKsAJJ_twoone_n 0.855
AKsAJT_twoone_n 0.95
AKsAJ9_twoone_n 0.81
AKsAJ8_twoone_n 0.9025
AKsAJ7_twoone_n 0.9025
AKsAJ6_twoone_n 0.81
AKsAJ5_twoone_n 0.855
AKsAJ4_twoone_n 0.9025
AKsAJ3_twoone_n 0.81
AKsAJ2_twoone_n 1.0
AKsAAT_twoone_n 1.0
AKsATT_twoone_n 0.855
AKsAT9_twoone_n 0.95
AKsAT8_twoone_n 0.765
AKsAT7_twoone_n 0.9025
AKsAT6_twoone_n 1.0
AKsAT5_twoone_n 1.0
AKsAT4_twoone_n 0.81
AKsAT3_twoone_n 0.95
AKsAT2_twoone_n 1.0
AKsAA9_twoone

In [142]:
def compute_rainbow_flop_effective_hand_strengths_for_suited_cards(iterations: int):
    name = "s"
    type = "_rainbow_"
    flush = "n"
    first_suit = "c"
    second_suit = "s"
    third_suit = "d"
    fourth_suit = "h"
    iterations_sq = iterations**2
    effective_hand_strengths = {}
    for starting_hand in itertools.combinations(list(Rank)[::-1], 2):
        deck = Deck()
        cards = np.concatenate(
            (
                deck.draw_card_by_tag(str(starting_hand[0].value) + first_suit),
                deck.draw_card_by_tag(str(starting_hand[1].value) + first_suit),
            )
        )
        # mono and flush
        rank_list = list(Rank)
        for combination in itertools.combinations_with_replacement(rank_list[::-1], 3):
            flop = np.concatenate(
                (
                    deck.draw_card_by_tag(str(combination[0].value) + second_suit),
                    deck.draw_card_by_tag(str(combination[1].value) + third_suit),
                    deck.draw_card_by_tag(str(combination[2].value) + fourth_suit),
                )
            )
            wins, positive_potential, negative_potential =  perform_n_posflop_iterations(iterations, deck, cards, flop)
            deck.return_cards(flop)
            effective_hand_strengths[
                str(starting_hand[0].value) + str(starting_hand[1].value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + type + flush
            ] = (
                wins * (iterations - negative_potential)
                + (iterations - wins) * positive_potential
            ) / iterations_sq
    return effective_hand_strengths

In [143]:
flop_effective_hand_strength_ranibow = compute_rainbow_flop_effective_hand_strengths_for_suited_cards(10)

In [144]:
for k,v in flop_effective_hand_strength_ranibow.items():
    print(k, v)

AKsAAA_rainbow_n 1.0
AKsAAK_rainbow_n 1.0
AKsAAQ_rainbow_n 1.0
AKsAAJ_rainbow_n 1.0
AKsAAT_rainbow_n 1.0
AKsAA9_rainbow_n 1.0
AKsAA8_rainbow_n 0.9025
AKsAA7_rainbow_n 0.95
AKsAA6_rainbow_n 0.9025
AKsAA5_rainbow_n 0.9025
AKsAA4_rainbow_n 0.9025
AKsAA3_rainbow_n 1.0
AKsAA2_rainbow_n 0.9025
AKsAKK_rainbow_n 1.0
AKsAKQ_rainbow_n 0.9025
AKsAKJ_rainbow_n 1.0
AKsAKT_rainbow_n 0.855
AKsAK9_rainbow_n 1.0
AKsAK8_rainbow_n 0.81
AKsAK7_rainbow_n 0.9025
AKsAK6_rainbow_n 0.9025
AKsAK5_rainbow_n 0.9025
AKsAK4_rainbow_n 0.9025
AKsAK3_rainbow_n 1.0
AKsAK2_rainbow_n 1.0
AKsAQQ_rainbow_n 1.0
AKsAQJ_rainbow_n 0.9025
AKsAQT_rainbow_n 0.9025
AKsAQ9_rainbow_n 0.95
AKsAQ8_rainbow_n 0.9025
AKsAQ7_rainbow_n 1.0
AKsAQ6_rainbow_n 0.9025
AKsAQ5_rainbow_n 0.81
AKsAQ4_rainbow_n 0.9025
AKsAQ3_rainbow_n 1.0
AKsAQ2_rainbow_n 0.64
AKsAJJ_rainbow_n 1.0
AKsAJT_rainbow_n 0.81
AKsAJ9_rainbow_n 0.9025
AKsAJ8_rainbow_n 0.81
AKsAJ7_rainbow_n 1.0
AKsAJ6_rainbow_n 0.855
AKsAJ5_rainbow_n 0.72
AKsAJ4_rainbow_n 0.855
AKsAJ3_rainbow

In [146]:
def compute_mono_flop_effective_hand_strengths_for_offsuit_cards_with_flush_draw(iterations: int, with_higher_card = True):
    name = "o"
    type = "_mono_"
    flush = "d_higher" if with_higher_card else "d_lower" 
    first_suit = "c"
    second_suit = "s"
    flush_suit = first_suit if with_higher_card else second_suit
    effective_hand_strengths = {}
    for starting_hand in itertools.combinations(list(Rank)[::-1], 2):
        deck = Deck()
        cards = np.concatenate(
            (
                deck.draw_card_by_tag(str(starting_hand[0].value) + first_suit),
                deck.draw_card_by_tag(str(starting_hand[1].value) + second_suit),
            )
        )
        rank_list = list(Rank)
        if with_higher_card:
            rank_list.remove(starting_hand[0])
        else:
            rank_list.remove(starting_hand[1])
        possible_combinations = itertools.combinations(rank_list[::-1], 3)
        for combination in possible_combinations:
            flop = np.concatenate(
                (
                    deck.draw_card_by_tag(str(combination[0].value) + flush_suit),
                    deck.draw_card_by_tag(str(combination[1].value) + flush_suit),
                    deck.draw_card_by_tag(str(combination[2].value) + flush_suit),
                )
            )
            wins, positive_potential, negative_potential = perform_n_posflop_iterations(iterations, deck, cards, flop)
            deck.return_cards(flop)
            if str(starting_hand[0].value) + str(starting_hand[1].value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush in effective_hand_strengths:
                raise ValueError(str(starting_hand[0].value) + str(starting_hand[1].value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush)
            effective_hand_strengths[
                str(starting_hand[0].value) + str(starting_hand[1].value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + type + flush
            ] = (
                wins * (iterations - negative_potential)
                + (iterations - wins) * positive_potential
            ) / iterations**2
    return effective_hand_strengths

In [147]:
flop_effective_hand_strength_offsuit_mono_flush_draw_with_higher = compute_mono_flop_effective_hand_strengths_for_offsuit_cards_with_flush_draw(10, True)
flop_effective_hand_strength_offsuit_mono_flush_draw_with_lower = compute_mono_flop_effective_hand_strengths_for_offsuit_cards_with_flush_draw(10, False)


In [148]:
def compute_mono_flop_effective_hand_strengths_for_pairs_with_flush_draw(iterations: int):
    name = "o"
    type = "_mono_"
    flush = "d"
    first_suit = "c"
    second_suit = "s"
    flush_suit = first_suit
    effective_hand_strengths = {}
    for rank_one in list(Rank)[::-1]:
        deck = Deck()
        cards = np.concatenate(
            (
                deck.draw_card_by_tag(str(rank_one.value) + first_suit),
                deck.draw_card_by_tag(str(rank_one.value) + second_suit),
            )
        )
        rank_list = list(Rank)
        rank_list.remove(rank_one)
        possible_combinations = itertools.combinations(rank_list[::-1], 3)
        for combination in possible_combinations:
            flop = np.concatenate(
                (
                    deck.draw_card_by_tag(str(combination[0].value) + flush_suit),
                    deck.draw_card_by_tag(str(combination[1].value) + flush_suit),
                    deck.draw_card_by_tag(str(combination[2].value) + flush_suit),
                )
            )
            wins, positive_potential, negative_potential = perform_n_posflop_iterations(iterations, deck, cards, flop)
            deck.return_cards(flop)
            if str(rank_one.value) + str(rank_one.value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush in effective_hand_strengths:
                raise ValueError(str(rank_one.value) + str(rank_one.value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush)
            effective_hand_strengths[
                str(rank_one.value) + str(rank_one.value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + type + flush
            ] = (
                wins * (iterations - negative_potential)
                + (iterations - wins) * positive_potential
            ) / iterations**2
    return effective_hand_strengths

In [149]:
flop_effective_hand_strength_pairs_mono_flush_draw = compute_mono_flop_effective_hand_strengths_for_pairs_with_flush_draw(10)


In [150]:
for k,v in flop_effective_hand_strength_pairs_mono_flush_draw.items():
    print(k, v)

AAoKQJ_mono_d 1.0
AAoKQT_mono_d 0.9025
AAoKQ9_mono_d 0.9525
AAoKQ8_mono_d 0.9525
AAoKQ7_mono_d 0.9525
AAoKQ6_mono_d 1.0
AAoKQ5_mono_d 1.0
AAoKQ4_mono_d 0.95
AAoKQ3_mono_d 0.9025
AAoKQ2_mono_d 0.855
AAoKJT_mono_d 1.0
AAoKJ9_mono_d 0.85
AAoKJ8_mono_d 1.0
AAoKJ7_mono_d 0.9025
AAoKJ6_mono_d 0.9025
AAoKJ5_mono_d 0.86
AAoKJ4_mono_d 1.0
AAoKJ3_mono_d 1.0
AAoKJ2_mono_d 0.95
AAoKT9_mono_d 0.95
AAoKT8_mono_d 0.9525
AAoKT7_mono_d 0.905
AAoKT6_mono_d 1.0
AAoKT5_mono_d 1.0
AAoKT4_mono_d 0.81
AAoKT3_mono_d 0.9
AAoKT2_mono_d 0.81
AAoK98_mono_d 0.9025
AAoK97_mono_d 0.95
AAoK96_mono_d 0.81
AAoK95_mono_d 0.9025
AAoK94_mono_d 0.95
AAoK93_mono_d 0.81
AAoK92_mono_d 1.0
AAoK87_mono_d 0.95
AAoK86_mono_d 0.9025
AAoK85_mono_d 1.0
AAoK84_mono_d 0.855
AAoK83_mono_d 0.855
AAoK82_mono_d 0.9025
AAoK76_mono_d 0.8075
AAoK75_mono_d 0.815
AAoK74_mono_d 0.9025
AAoK73_mono_d 1.0
AAoK72_mono_d 1.0
AAoK65_mono_d 0.81
AAoK64_mono_d 0.7725
AAoK63_mono_d 0.9525
AAoK62_mono_d 1.0
AAoK54_mono_d 1.0
AAoK53_mono_d 0.9025
AAoK52_m

In [41]:
for k,v in flop_effective_hand_strength_offsuit_mono_flush_draw_with_lower.items():
    print(k, v)

AKoAQJrd_lower 0.8075
AKoAQTrd_lower 1.0
AKoAQ9rd_lower 1.0
AKoAQ8rd_lower 1.0
AKoAQ7rd_lower 1.0
AKoAQ6rd_lower 1.0
AKoAQ5rd_lower 0.905
AKoAQ4rd_lower 0.9025
AKoAQ3rd_lower 1.0
AKoAQ2rd_lower 0.9525
AKoAJTrd_lower 1.0
AKoAJ9rd_lower 1.0
AKoAJ8rd_lower 0.86
AKoAJ7rd_lower 0.905
AKoAJ6rd_lower 0.9025
AKoAJ5rd_lower 0.95
AKoAJ4rd_lower 0.9
AKoAJ3rd_lower 0.95
AKoAJ2rd_lower 0.815
AKoAT9rd_lower 1.0
AKoAT8rd_lower 0.855
AKoAT7rd_lower 0.9025
AKoAT6rd_lower 0.855
AKoAT5rd_lower 1.0
AKoAT4rd_lower 0.95
AKoAT3rd_lower 1.0
AKoAT2rd_lower 0.855
AKoA98rd_lower 0.81
AKoA97rd_lower 0.855
AKoA96rd_lower 0.72
AKoA95rd_lower 1.0
AKoA94rd_lower 1.0
AKoA93rd_lower 1.0
AKoA92rd_lower 0.81
AKoA87rd_lower 1.0
AKoA86rd_lower 0.9025
AKoA85rd_lower 0.9025
AKoA84rd_lower 0.9025
AKoA83rd_lower 0.81
AKoA82rd_lower 0.9525
AKoA76rd_lower 1.0
AKoA75rd_lower 0.855
AKoA74rd_lower 0.81
AKoA73rd_lower 1.0
AKoA72rd_lower 0.765
AKoA65rd_lower 0.86
AKoA64rd_lower 0.9025
AKoA63rd_lower 0.9525
AKoA62rd_lower 0.95
AKoA54r

In [151]:
def compute_21_flop_effective_hand_strengths_for_offsuit_cards(iterations: int):
    name = "o"
    flush = "n"
    first_suit = "c"
    second_suit = "s"
    third_suit = "d"
    fourth_suit = "h"
    
        
    effective_hand_strengths = {}
    for starting_hand in itertools.combinations(list(Rank)[::-1], 2):
        deck = Deck()
        cards = np.concatenate(
            (
                deck.draw_card_by_tag(str(starting_hand[0].value) + first_suit),
                deck.draw_card_by_tag(str(starting_hand[1].value) + second_suit),
            )
        )
        rank_list = list(Rank)
        possible_combinations = itertools.combinations(rank_list[::-1], 2)
        for combination in possible_combinations:
            third_suit_rank_list = [combination[0], combination[1]] + create_a_list_of_lower_ranks(combination[1])[::-1]
            for rank in third_suit_rank_list:
                flop = np.concatenate(
                    (
                        deck.draw_card_by_tag(str(combination[0].value) + third_suit),
                        deck.draw_card_by_tag(str(combination[1].value) + third_suit),
                        deck.draw_card_by_tag(str(rank.value) + fourth_suit),
                    )
                )
                flop = sort_hand(flop)
                wins, positive_potential, negative_potential = perform_n_posflop_iterations(iterations, deck, cards, flop)
                deck.return_cards(flop)
                if str(starting_hand[0].value) + str(starting_hand[1].value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush in effective_hand_strengths:
                    raise ValueError(str(starting_hand[0].value) + str(starting_hand[1].value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush)
                effective_hand_strengths[
                    str(starting_hand[0].value) + str(starting_hand[1].value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush
                ] = (
                    wins * (iterations - negative_potential)
                    + (iterations - wins) * positive_potential
                ) / iterations**2
    return effective_hand_strengths

In [152]:
def compute_21_flop_effective_hand_strengths_for_pairs(iterations: int):
    name = "o"
    flush = "n"
    first_suit = "c"
    second_suit = "s"
    third_suit = "d"
    fourth_suit = "h"
    
        
    effective_hand_strengths = {}
    for rank_one in list(Rank)[::-1]:
        rank_two = rank_one
        deck = Deck()
        cards = np.concatenate(
            (
                deck.draw_card_by_tag(str(rank_one.value) + first_suit),
                deck.draw_card_by_tag(str(rank_two.value) + second_suit),
            )
        )
        rank_list = list(Rank)
        for combination in itertools.combinations(rank_list[::-1], 2):
            third_suit_rank_list = [combination[0], combination[1]] + create_a_list_of_lower_ranks(combination[1])[::-1]
            for rank in third_suit_rank_list:
                flop = np.concatenate(
                    (
                        deck.draw_card_by_tag(str(combination[0].value) + third_suit),
                        deck.draw_card_by_tag(str(combination[1].value) + third_suit),
                        deck.draw_card_by_tag(str(rank.value) + fourth_suit),
                    )
                )
                flop = sort_hand(flop)
                wins, positive_potential, negative_potential = perform_n_posflop_iterations(iterations, deck, cards, flop)
                deck.return_cards(flop)
                if str(rank_one.value) + str(rank_two.value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush in effective_hand_strengths:
                    raise ValueError(str(rank_one.value) + str(rank_two.value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush)
                effective_hand_strengths[
                    str(rank_one.value) + str(rank_two.value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush
                ] = (
                    wins * (iterations - negative_potential)
                    + (iterations - wins) * positive_potential
                ) / iterations**2
    return effective_hand_strengths

In [153]:
effective_hand_strengths_21_flop_for_offsuit_cards = compute_21_flop_effective_hand_strengths_for_offsuit_cards(10)
effective_hand_strengths_21_flop_for_pairs = compute_21_flop_effective_hand_strengths_for_pairs(10)
for k,v in effective_hand_strengths_21_flop_for_offsuit_cards.items():
    print(k, v)


AKoAAKtn 1.0
AKoAKKtn 1.0
AKoAKQtn 0.9025
AKoAKJtn 0.9025
AKoAKTtn 1.0
AKoAK9tn 1.0
AKoAK8tn 1.0
AKoAK7tn 0.9025
AKoAK6tn 0.9025
AKoAK5tn 1.0
AKoAK4tn 0.9025
AKoAK3tn 0.9025
AKoAK2tn 0.9025
AKoAAQtn 0.81
AKoAQQtn 1.0
AKoAQJtn 0.765
AKoAQTtn 0.6
AKoAQ9tn 0.95
AKoAQ8tn 0.81
AKoAQ7tn 0.855
AKoAQ6tn 0.7225
AKoAQ5tn 0.7225
AKoAQ4tn 0.81
AKoAQ3tn 0.905
AKoAQ2tn 0.9025
AKoAAJtn 1.0
AKoAJJtn 0.95
AKoAJTtn 0.95
AKoAJ9tn 0.81
AKoAJ8tn 0.81
AKoAJ7tn 1.0
AKoAJ6tn 1.0
AKoAJ5tn 0.81
AKoAJ4tn 1.0
AKoAJ3tn 0.765
AKoAJ2tn 1.0
AKoAATtn 1.0
AKoATTtn 0.95
AKoAT9tn 0.9025
AKoAT8tn 0.68
AKoAT7tn 0.81
AKoAT6tn 1.0
AKoAT5tn 0.9025
AKoAT4tn 0.81
AKoAT3tn 1.0
AKoAT2tn 0.855
AKoAA9tn 0.95
AKoA99tn 0.8075
AKoA98tn 1.0
AKoA97tn 0.81
AKoA96tn 1.0
AKoA95tn 0.81
AKoA94tn 0.9525
AKoA93tn 0.68
AKoA92tn 0.7225
AKoAA8tn 1.0
AKoA88tn 0.8075
AKoA87tn 0.81
AKoA86tn 0.9025
AKoA85tn 0.81
AKoA84tn 1.0
AKoA83tn 0.81
AKoA82tn 1.0
AKoAA7tn 1.0
AKoA77tn 0.9025
AKoA76tn 0.64
AKoA75tn 0.9025
AKoA74tn 0.81
AKoA73tn 0.6375
AKoA72tn 0.

In [154]:
for k,v in effective_hand_strengths_21_flop_for_pairs.items():
    print(k, v)

AAoAAKtn 1.0
AAoAKKtn 1.0
AAoAKQtn 0.81
AAoAKJtn 0.9025
AAoAKTtn 0.9025
AAoAK9tn 1.0
AAoAK8tn 1.0
AAoAK7tn 0.9025
AAoAK6tn 1.0
AAoAK5tn 1.0
AAoAK4tn 0.9025
AAoAK3tn 1.0
AAoAK2tn 0.9025
AAoAAQtn 1.0
AAoAQQtn 1.0
AAoAQJtn 0.9025
AAoAQTtn 1.0
AAoAQ9tn 1.0
AAoAQ8tn 1.0
AAoAQ7tn 0.7225
AAoAQ6tn 1.0
AAoAQ5tn 0.9025
AAoAQ4tn 0.9025
AAoAQ3tn 0.9025
AAoAQ2tn 1.0
AAoAAJtn 1.0
AAoAJJtn 1.0
AAoAJTtn 0.9025
AAoAJ9tn 0.9025
AAoAJ8tn 0.81
AAoAJ7tn 1.0
AAoAJ6tn 1.0
AAoAJ5tn 0.9025
AAoAJ4tn 1.0
AAoAJ3tn 1.0
AAoAJ2tn 1.0
AAoAATtn 1.0
AAoATTtn 1.0
AAoAT9tn 0.9025
AAoAT8tn 0.9025
AAoAT7tn 0.9025
AAoAT6tn 1.0
AAoAT5tn 1.0
AAoAT4tn 1.0
AAoAT3tn 0.9025
AAoAT2tn 1.0
AAoAA9tn 1.0
AAoA99tn 1.0
AAoA98tn 1.0
AAoA97tn 1.0
AAoA96tn 0.9025
AAoA95tn 0.9025
AAoA94tn 1.0
AAoA93tn 1.0
AAoA92tn 0.9025
AAoAA8tn 1.0
AAoA88tn 1.0
AAoA87tn 0.9025
AAoA86tn 0.9025
AAoA85tn 0.9025
AAoA84tn 0.81
AAoA83tn 0.9025
AAoA82tn 1.0
AAoAA7tn 1.0
AAoA77tn 0.95
AAoA76tn 0.81
AAoA75tn 0.81
AAoA74tn 0.81
AAoA73tn 0.9025
AAoA72tn 1.0
AAoAA6tn

In [156]:
def compute_rainbow_flop_effective_hand_strengths_for_offsuit_cards(iterations: int):
    name = "o"
    type = "r"
    flush = "n"
    first_suit = "c"
    second_suit = "s"
    third_suit = "d"
    fourth_suit = "h"
    iterations_sq = iterations**2
    effective_hand_strengths = {}
    for starting_hand in itertools.combinations(list(Rank)[::-1], 2):
        deck = Deck()
        cards = np.concatenate(
            (
                deck.draw_card_by_tag(str(starting_hand[0].value) + first_suit),
                deck.draw_card_by_tag(str(starting_hand[1].value) + second_suit),
            )
        )
        rank_list = list(Rank)
        for combination in itertools.combinations_with_replacement(rank_list[::-1], 3):
            temp_suit = first_suit if combination[0] != starting_hand[0] else second_suit
            flop = np.concatenate(
                (
                    deck.draw_card_by_tag(str(combination[0].value) + temp_suit),
                    deck.draw_card_by_tag(str(combination[1].value) + third_suit),
                    deck.draw_card_by_tag(str(combination[2].value) + fourth_suit),
                )
            )
            wins, positive_potential, negative_potential = perform_n_posflop_iterations(iterations, deck, cards, flop)
            deck.return_cards(flop)
            if str(starting_hand[0].value) + str(starting_hand[1].value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush in effective_hand_strengths:
                raise ValueError(str(starting_hand[0].value) + str(starting_hand[1].value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush)
            effective_hand_strengths[
                str(starting_hand[0].value) + str(starting_hand[1].value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + type + flush
            ] = (
                wins * (iterations - negative_potential)
                + (iterations - wins) * positive_potential
            ) / iterations_sq
    return effective_hand_strengths

In [157]:
effective_hand_strengths_rainbow_flop_for_offsuit_cards = compute_rainbow_flop_effective_hand_strengths_for_offsuit_cards(10)
for k,v in effective_hand_strengths_rainbow_flop_for_offsuit_cards.items():
    print(k, v)

AKoAAArn 1.0
AKoAAKrn 1.0
AKoAAQrn 1.0
AKoAAJrn 1.0
AKoAATrn 1.0
AKoAA9rn 1.0
AKoAA8rn 1.0
AKoAA7rn 1.0
AKoAA6rn 1.0
AKoAA5rn 1.0
AKoAA4rn 0.9025
AKoAA3rn 0.95
AKoAA2rn 1.0
AKoAKKrn 1.0
AKoAKQrn 1.0
AKoAKJrn 0.95
AKoAKTrn 0.9025
AKoAK9rn 1.0
AKoAK8rn 0.9025
AKoAK7rn 0.765
AKoAK6rn 1.0
AKoAK5rn 1.0
AKoAK4rn 1.0
AKoAK3rn 0.9025
AKoAK2rn 0.9025
AKoAQQrn 1.0
AKoAQJrn 0.81
AKoAQTrn 1.0
AKoAQ9rn 0.81
AKoAQ8rn 0.81
AKoAQ7rn 1.0
AKoAQ6rn 0.95
AKoAQ5rn 0.9025
AKoAQ4rn 0.765
AKoAQ3rn 0.81
AKoAQ2rn 1.0
AKoAJJrn 1.0
AKoAJTrn 0.81
AKoAJ9rn 0.9025
AKoAJ8rn 0.765
AKoAJ7rn 1.0
AKoAJ6rn 1.0
AKoAJ5rn 0.9025
AKoAJ4rn 0.855
AKoAJ3rn 0.81
AKoAJ2rn 0.81
AKoATTrn 0.95
AKoAT9rn 0.765
AKoAT8rn 0.81
AKoAT7rn 0.7225
AKoAT6rn 0.95
AKoAT5rn 0.9025
AKoAT4rn 0.7225
AKoAT3rn 0.9025
AKoAT2rn 0.95
AKoA99rn 0.95
AKoA98rn 0.9025
AKoA97rn 0.81
AKoA96rn 0.9025
AKoA95rn 1.0
AKoA94rn 1.0
AKoA93rn 1.0
AKoA92rn 0.9025
AKoA88rn 0.8075
AKoA87rn 0.9025
AKoA86rn 1.0
AKoA85rn 0.81
AKoA84rn 0.905
AKoA83rn 1.0
AKoA82rn 0.9025
AKoA77r

In [158]:
def compute_rainbow_flop_effective_hand_strengths_for_pairs(iterations: int):
    name = "o"
    type = "r"
    flush = "n"
    first_suit = "c"
    second_suit = "s"
    third_suit = "d"
    fourth_suit = "h"
    iterations_sq = iterations**2
    effective_hand_strengths = {}
    for rank_one in list(Rank)[::-1]:
        rank_two = rank_one
        deck = Deck()
        cards = np.concatenate(
            (
                deck.draw_card_by_tag(str(rank_one.value) + first_suit),
                deck.draw_card_by_tag(str(rank_two.value) + second_suit),
            )
        )
        rank_list = list(Rank)
        for combination in itertools.combinations_with_replacement(rank_list[::-1], 3):
            if combination[0] == combination[2] and rank_one == combination[0]:
                continue
            if combination[0] == rank_one:
                temp_suit_one = third_suit
                temp_suit_two = fourth_suit
                temp_suit_three = first_suit
            else:
                temp_suit_one = first_suit
                temp_suit_two = third_suit
                temp_suit_three = fourth_suit
            flop = np.concatenate(
                (
                    deck.draw_card_by_tag(str(combination[0].value) + temp_suit_one),
                    deck.draw_card_by_tag(str(combination[1].value) + temp_suit_two),
                    deck.draw_card_by_tag(str(combination[2].value) + temp_suit_three),
                )
            )
            wins, positive_potential, negative_potential = perform_n_posflop_iterations(iterations, deck, cards, flop)
            deck.return_cards(flop)
            if str(rank_one.value) + str(rank_two.value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush in effective_hand_strengths:
                raise ValueError(str(rank_one.value) + str(rank_two.value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + "t" + flush)
            effective_hand_strengths[
                str(rank_one.value) + str(rank_two.value) + name + str(flop[0].rank.value) + str(flop[1].rank.value) + str(flop[2].rank.value) + type + flush
            ] = (
                wins * (iterations - negative_potential)
                + (iterations - wins) * positive_potential
            ) / iterations_sq
    return effective_hand_strengths

In [159]:
effective_hand_strengths_rainbow_flop_for_pairs = compute_rainbow_flop_effective_hand_strengths_for_pairs(10)
for k,v in effective_hand_strengths_rainbow_flop_for_pairs.items():
    print(k, v)

AAoAAKrn 1.0
AAoAAQrn 1.0
AAoAAJrn 1.0
AAoAATrn 1.0
AAoAA9rn 1.0
AAoAA8rn 1.0
AAoAA7rn 1.0
AAoAA6rn 1.0
AAoAA5rn 1.0
AAoAA4rn 1.0
AAoAA3rn 1.0
AAoAA2rn 1.0
AAoAKKrn 0.9025
AAoAKQrn 1.0
AAoAKJrn 1.0
AAoAKTrn 1.0
AAoAK9rn 1.0
AAoAK8rn 1.0
AAoAK7rn 0.9025
AAoAK6rn 0.81
AAoAK5rn 0.81
AAoAK4rn 1.0
AAoAK3rn 1.0
AAoAK2rn 0.9025
AAoAQQrn 1.0
AAoAQJrn 0.81
AAoAQTrn 0.9025
AAoAQ9rn 0.9025
AAoAQ8rn 0.9025
AAoAQ7rn 1.0
AAoAQ6rn 0.9025
AAoAQ5rn 0.9025
AAoAQ4rn 0.9025
AAoAQ3rn 1.0
AAoAQ2rn 0.9025
AAoAJJrn 0.9025
AAoAJTrn 0.7225
AAoAJ9rn 0.9025
AAoAJ8rn 0.7225
AAoAJ7rn 1.0
AAoAJ6rn 1.0
AAoAJ5rn 1.0
AAoAJ4rn 1.0
AAoAJ3rn 1.0
AAoAJ2rn 0.9025
AAoATTrn 1.0
AAoAT9rn 0.9025
AAoAT8rn 0.9025
AAoAT7rn 1.0
AAoAT6rn 1.0
AAoAT5rn 0.81
AAoAT4rn 1.0
AAoAT3rn 1.0
AAoAT2rn 1.0
AAoA99rn 1.0
AAoA98rn 0.9025
AAoA97rn 0.81
AAoA96rn 1.0
AAoA95rn 0.81
AAoA94rn 1.0
AAoA93rn 1.0
AAoA92rn 1.0
AAoA88rn 1.0
AAoA87rn 1.0
AAoA86rn 1.0
AAoA85rn 1.0
AAoA84rn 0.9025
AAoA83rn 1.0
AAoA82rn 1.0
AAoA77rn 1.0
AAoA76rn 1.0
AAoA75rn 0.81


In [142]:
import json

In [143]:
with open("preflop_ehs.json", 'w') as f:
    json.dump(effective_hand_strength, f)

In [144]:
with open("postflop_mono_and_flush_ehs.json", 'w') as f:
    json.dump(flop_effective_hand_strength_mono_and_flush, f)

In [145]:
with open("postflop_mono_and_nothing_ehs.json", 'w') as f:
    json.dump(flop_effective_hand_strength_mono_and_nothing, f)

In [147]:
with open("postflop_two_one_flush_draw_ehs.json", 'w') as f:
    cards_strength = json.dump(flop_effective_hand_strength_two_one_and_flush_draw, f)

In [20]:
for k,v in sorted(cards_strength.items(), key=lambda item: item[1], reverse=True):
    print(k, v)

AAo 0.72504093115
KKo 0.68305080385
QQo 0.6488844208
54s 0.62793650675
65s 0.6257558772
76s 0.61852472975
53s 0.615117073125
64s 0.609163682
87s 0.6090829165
43s 0.608722533225
JJo 0.606115846975
75s 0.605527336425
98s 0.5988284916
86s 0.5968488013
52s 0.5948646311
42s 0.593194550125
63s 0.592384529175
32s 0.590392840475
74s 0.59015805285
T9s 0.5888193465
97s 0.5873583335
65o 0.586740245
54o 0.584789117
85s 0.5838598725
76o 0.5832674056
TTo 0.5775377743
87o 0.5767724845
T8s 0.57271780425
53o 0.57094552
JTs 0.5709050045
73s 0.570624126525
96s 0.570377951725
62s 0.57033191925
64o 0.569510728175
75o 0.56879458625
98o 0.56725181775
43o 0.567115602725
84s 0.56630449025
86o 0.562895108
T9o 0.56147025195
T7s 0.56061226115
72s 0.55846408525
95s 0.5582394128
J9s 0.5581327684
97o 0.5535281234
83s 0.5519820212
63o 0.55055055395
52o 0.5498880227
82s 0.54964569745
T6s 0.5483649832
74o 0.5471063256
JTo 0.54600591625
85o 0.545953219225
QJs 0.544317586
42o 0.544100115025
T8o 0.5430129977
32o 0.5429029

In [37]:
max_std = max([x[1] for x in cards_strength.values()])
min_std = min([x[1] for x in cards_strength.values()])

In [38]:
print(max_std, min_std)

1912.0 984.0


In [34]:
for k,v in cards_strength.items():
    cards_strength[k] = (v[0], round((v[1] - min_std) / (max_std - min_std), 3))

In [35]:
for k,v in sorted(cards_strength.items(), key=lambda item: item[1][0]):
    print(k,v)

AAo (2457.0, 0.0)
KKo (2599.0, 0.062)
QQo (2713.0, 0.142)
JJo (2825.0, 0.214)
TTo (2930.0, 0.297)
99o (3033.0, 0.377)
88o (3130.0, 0.458)
77o (3234.0, 0.545)
66o (3319.0, 0.627)
55o (3411.0, 0.718)
44o (3516.0, 0.811)
33o (3622.0, 0.903)
AKs (3671.0, 0.852)
AQs (3713.0, 0.856)
22o (3723.0, 0.998)
AJs (3737.0, 0.855)
ATs (3756.0, 0.859)
KQs (3764.0, 0.88)
JTs (3789.0, 0.905)
KJs (3795.0, 0.881)
QJs (3795.0, 0.897)
KTs (3800.0, 0.891)
QTs (3807.0, 0.903)
A9s (3830.0, 0.853)
A8s (3839.0, 0.852)
T9s (3846.0, 0.905)
AKo (3862.0, 0.721)
A7s (3864.0, 0.865)
A5s (3868.0, 0.897)
J9s (3869.0, 0.895)
Q9s (3881.0, 0.886)
K9s (3886.0, 0.876)
98s (3896.0, 0.904)
A6s (3903.0, 0.873)
AQo (3906.0, 0.726)
A4s (3907.0, 0.913)
T8s (3911.0, 0.899)
AJo (3933.0, 0.737)
J8s (3933.0, 0.891)
A3s (3938.0, 0.92)
87s (3943.0, 0.915)
ATo (3948.0, 0.736)
K7s (3950.0, 0.878)
KQo (3953.0, 0.786)
K8s (3953.0, 0.874)
97s (3954.0, 0.906)
Q8s (3956.0, 0.887)
KJo (3960.0, 0.789)
QJo (3961.0, 0.824)
A2s (3966.0, 0.95)
JTo (

In [56]:
deck = Deck()
deck.shuffle()
cards = np.concatenate((deck.draw_card_by_tag("Qc"), deck.draw_card_by_tag("Qs"), deck.draw_card_by_tag("Qd"), deck.draw_card_by_tag("Qh")))

In [57]:
sorted(cards, reverse=True, key=lambda x: (x, x.get_tag()))

[Queen of Clubs, Queen of Spades, Queen of Diamonds, Queen of Hearts]